# 🇪🇺 🏷️ Eurovoc Model Training Notebook

In [1]:
import pickle 
import pandas as pd
from transformers import AutoTokenizer, AutoModel

from datasets import list_datasets, load_dataset

from sklearn.preprocessing import MultiLabelBinarizer
import torch

import pytorch_lightning as pl
from pytorch_lightning.callbacks import ModelCheckpoint

---

## 1. Data loading
### Choose our dataset, extracted from ep registry or eurlex57k

In [2]:
#dataset = load_dataset('json', data_files='ep_registry.jsonl')

#dataset = load_dataset('eurlex')
dataset = load_dataset('EuropeanParliament/cellar_eurovoc')


Found cached dataset json (/home/scampion/.cache/huggingface/datasets/EuropeanParliament___json/EuropeanParliament--cellar_eurovoc-3a27a019ebbf0296/0.0.0/8bb11242116d547c741b2e8a1f18598ffdd40a1d4f2a2872c7a28b697434bc96)


  0%|          | 0/1 [00:00<?, ?it/s]

### Merge train, test and validation

In [3]:
train = dataset['train'].to_pandas()
test = dataset['test'].to_pandas() if 'test' in dataset.keys() else None
validation = dataset['validation'].to_pandas() if 'validation' in dataset.keys() else None

all = pd.concat([train, test, validation])#[:1000]
all.head()

title       date  \
0  Corrigendum to Commission Implementing Regulat... 2023-07-20   
1  Council Decision (CFSP) 2023/1501 of 20 July 2... 2023-07-20   
2  Council Decision (CFSP) 2023/1502 of 20 July 2... 2023-07-20   
3  The Committee of the Regions welcomes Croatian... 2023-07-20   
4  Corrigendum to Commission Implementing Regulat... 2023-07-20   

                                    eurovoc_concepts  \
0  [China, Malaysia, anti-dumping duty, business ...   
1  [EU restrictive measure, Russia, Ukraine, econ...   
2  [Burma/Myanmar, EU restrictive measure, econom...   
3  [Croatia, EU regional policy, European Committ...   
4  [India, Türkiye, anti-dumping duty, building m...   

                                                 url lang  \
0  http://publications.europa.eu/resource/cellar/...  eng   
1  http://publications.europa.eu/resource/cellar/...  eng   
2  http://publications.europa.eu/resource/cellar/...  eng   
3  http://publications.europa.eu/resource/cellar/...  eng   
4  http://publications.europa.eu/resource/cellar/...  eng   

                 formats                                               text  
0  [fmx4, pdfa2a, xhtml]  L_2023183EN. 01005801. xml 20. 7. 2023    EN O...  
1  [fmx4, pdfa2a, xhtml]  LI2023183EN. 01004801. xml 20. 7. 2023    EN O...  
2  [fmx4, pdfa2a, xhtml]  LI2023183EN. 01005201. xml 20. 7. 2023    EN O...  
3                  [pdf]  EUROPEAN UNION Committee of the Regions The Co...  
4  [fmx4, pdfa2a, xhtml]  L_2023183EN. 01005901. xml 20. 7. 2023    EN O...

In [4]:
#all['eurovoc_concepts_str'] = all['eurovoc_concepts'].apply(str)

### Create the MultiLabel Binarizer and save it in a file for prediction

In [4]:
mlb = MultiLabelBinarizer().fit(all['eurovoc_concepts'])

pickle.dump(mlb, open('mlb.pickle', 'wb'))
"Number of classes", len(mlb.classes_)

('Number of classes', 6835)

---
## 2. Split data using iterative train test 

In [ ]:
import numpy as np
#X = np.array(all['text'].to_list())
#X = np.expand_dims(X, axis=1)
X = all['text'].to_numpy()
X = np.expand_dims(X, axis=1)
y = mlb.transform(all['eurovoc_concepts'])


from skmultilearn.model_selection import iterative_train_test_split
x_tr, y_tr, x_test, y_test = iterative_train_test_split(X, y, test_size = 0.1)
x_tr, y_tr, x_val, y_val = iterative_train_test_split(x_tr, y_tr, test_size = 0.1)
len(x_tr), len(x_val), len(x_test)

In [ ]:
# Example 
i = 10
x_tr[i][0][0:120], mlb.inverse_transform(np.expand_dims(y_tr[i], axis=1).T)

---
## 3. Model definition and training

In [ ]:
%%capture output
%load_ext autoreload
%autoreload 2

from eurovoc import EurovocTagger, EurovocDataset, EurovocDataModule


BERT_MODEL_NAME = "nlpaueb/legal-bert-base-uncased"
N_EPOCHS = 30
BATCH_SIZE = 10
MAX_LEN = 512
LR = 5e-05


# Instantiate and set up the data_module
dataloader = EurovocDataModule(BERT_MODEL_NAME, x_tr, y_tr, x_val, y_val , BATCH_SIZE, MAX_LEN)
dataloader.setup()


model = EurovocTagger(BERT_MODEL_NAME, len(mlb.classes_), lr=LR)

checkpoint_callback = ModelCheckpoint(
    monitor='val_loss',
    filename='EurovocTagger-{epoch:02d}-{val_loss:.2f}',
    mode='min',
)

trainer = pl.Trainer(max_epochs=N_EPOCHS , accelerator="gpu", devices=1, callbacks=[checkpoint_callback])#,strategy="ddp_notebook")
trainer.fit(model, dataloader)

Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 

In [13]:
trainer.save_checkpoint("eurovoc_cellar.ckpt")

In [ ]:
output()

In [14]:
np.save('x_test', x_test)
np.save('y_test', y_test)

In [15]:
trainer.test(dataloaders=dataloader)

/home/scampion/training/venv/lib/python3.10/site-packages/pytorch_lightning/trainer/connectors/checkpoint_connector.py:148: UserWarning: `.test(ckpt_path=None)` was called without a model. The best model of the previous `fit` call will be used. You can pass `.test(ckpt_path='best')` to use the best model or `.test(ckpt_path='last')` to use the last model. If you pass a value, this warning will be silenced.
  rank_zero_warn(
Restoring states from the checkpoint path at /home/scampion/training/lightning_logs/version_9/checkpoints/EurovocTagger-epoch=06-val_loss=0.00.ckpt
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2]
Loaded model weights from the checkpoint at /home/scampion/training/lightning_logs/version_9/checkpoints/EurovocTagger-epoch=06-val_loss=0.00.ckpt
/home/scampion/training/venv/lib/python3.10/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:432: PossibleUserWarning: The dataloader, test_dataloader, does not have many workers which may be a bottleneck. Consi

Testing: 0it [00:00, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│         test_loss         │   0.0031269278842955828   │
└───────────────────────────┴───────────────────────────┘

[{'test_loss': 0.0031269278842955828}]

# Evaluation

In [16]:
best_model_path = trainer.checkpoint_callback.best_model_path
best_model_path

'/home/scampion/training/lightning_logs/version_9/checkpoints/EurovocTagger-epoch=06-val_loss=0.00.ckpt'

In [17]:
from tqdm import tqdm
from transformers import AutoTokenizer

trained_model = EurovocTagger.load_from_checkpoint(best_model_path,
                                                   bert_model_name=BERT_MODEL_NAME,
                                                   n_classes=len(mlb.classes_))
trained_model.eval()
trained_model.freeze()

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
trained_model = trained_model.to(device)

tokenizer = AutoTokenizer.from_pretrained(BERT_MODEL_NAME)

val_dataset = EurovocDataset(x_test, y_test, tokenizer, max_token_len=MAX_LEN)
predictions = []
labels = []

for item in tqdm(val_dataset):
  _, prediction = trained_model(
    item["input_ids"].unsqueeze(dim=0).to(device), 
    item["attention_mask"].unsqueeze(dim=0).to(device)
  )
  predictions.append(prediction.flatten())
  labels.append(item["labels"].int())

predictions = torch.stack(predictions).detach().cpu()
labels = torch.stack(labels).detach().cpu()

Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|██████████| 23243/23243 [16:20<00:00, 23.72it/s]  


### F1 Score

In [18]:
from torchmetrics import F1Score
for i in range(1, 70, 5):
    f1 = F1Score(task="multilabel", num_labels=len(mlb.classes_),  average='weighted', threshold= i / 100.0)
    print(i / 100.0, f1(predictions, labels))

0.01 tensor(0.2188)
0.06 tensor(0.3929)
0.11 tensor(0.4353)
0.16 tensor(0.4462)
0.21 tensor(0.4437)
0.26 tensor(0.4364)
0.31 tensor(0.4249)
0.36 tensor(0.4106)
0.41 tensor(0.3947)
0.46 tensor(0.3780)
0.51 tensor(0.3597)
0.56 tensor(0.3404)
0.61 tensor(0.3209)
0.66 tensor(0.3007)


### NDCG Score

In [ ]:
from sklearn.metrics import ndcg_score
def calculate_average_ndcg(predictions, labels, top_k=5):
    # Initialize a list to store NDCG scores for each sample
    ndcg_scores = []

    # Calculate NDCG for each sample
    for i in range(len(predictions)):
        # Convert tensors to numpy arrays
        y_true = labels[i].cpu().numpy().reshape(1, -1)
        y_score = predictions[i].cpu().numpy().reshape(1, -1)
        
        # Calculate NDCG for the sample
        ndcg = ndcg_score(y_true, y_score, k=top_k)
        ndcg_scores.append(ndcg)

    # Calculate the average NDCG score
    average_ndcg = np.mean(ndcg_scores)
    
    return average_ndcg

for k in [3, 5, 10]:
    average = calculate_average_ndcg(predictions, labels, top_k=k)
    print("NDCG@"+str(k)+": "+ str(round(average, 4)))